# Business Data Challenge - Team 1

In [1]:
import pandas as pd
import numpy as np
import os
import s3fs
import re
import warnings

Configuration de l'accès aux données

In [2]:
# Create filesystem object
S3_ENDPOINT_URL = "https://" + os.environ["AWS_S3_ENDPOINT"]
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url': S3_ENDPOINT_URL})

In [41]:
# Create filesystem object
S3_ENDPOINT_URL = "https://" + os.environ["AWS_S3_ENDPOINT"]
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url': S3_ENDPOINT_URL})


# Import cleaning and merge functions

exec(open('0_Cleaning_and_merge_functions.py').read())

exec(open('0_KPI_functions.py').read())

# Ignore warning
warnings.filterwarnings('ignore')


In [4]:
def load_dataset_2(directory_path, file_name):
    """
    This function loads csv file
    """
    file_path = "bdc2324-data" + "/" + directory_path + "/" + directory_path + file_name + ".csv"
    with fs.open(file_path, mode="rb") as file_in:
        df = pd.read_csv(file_in, sep=",")

    # drop na :
    #df = df.dropna(axis=1, thresh=len(df))
    # if identifier in table : delete it
    if 'identifier' in df.columns:
        df = df.drop(columns = 'identifier')
    return df

In [36]:
def export_in_temporary(df, output_name):
    print('Export of dataset :', output_name)
    FILE_PATH_OUT_S3 = "projet-bdc2324-team1/Temporary" + "/" + output_name + '.csv'
    with fs.open(FILE_PATH_OUT_S3, 'w') as file_out:
        df.to_csv(file_out, index = False)

# Cleaning target area and tags

In [23]:
target_example = preprocessing_target_area('1')

File path :  bdc2324-data/1/1targets.csv
Shape :  (287, 5)
Number of columns :  3
Columns :  Index(['id', 'target_type_id', 'name'], dtype='object')
File path :  bdc2324-data/1/1target_types.csv
Shape :  (4, 6)
Number of columns :  4
Columns :  Index(['id', 'identifier', 'is_import', 'name'], dtype='object')
File path :  bdc2324-data/1/1customer_target_mappings.csv
Shape :  (768024, 7)
Number of columns :  5
Columns :  Index(['id', 'customer_id', 'target_id', 'name', 'extra_field'], dtype='object')


In [24]:
target_example

id  customer_id                    target_name  \
0       1184824       645400       DDCP PROMO Réseau livres   
1       1184825       645400  Inscrits NL générale site web   
2       1184828       645402    DDCP PROMO Art contemporain   
3       1184829       645403    DDCP PROMO Art contemporain   
4       1295770       647301           Votre première liste   
...         ...          ...                            ...   
768019  2737545       666983  Inscrits NL générale site web   
768020  2737546       666983           Votre première liste   
768021  2737575       666986           Votre première liste   
768022  2737576       666987  Inscrits NL générale site web   
768023  2737577       666987           Votre première liste   

        target_type_is_import      target_type_name  
0                       False  manual_static_filter  
1                       False  manual_static_filter  
2                       False  manual_static_filter  
3                       False  manual_static_filter  
4                       False  manual_static_filter  
...                       ...                   ...  
768019                  False  manual_static_filter  
768020                  False  manual_static_filter  
768021                  False  manual_static_filter  
768022                  False  manual_static_filter  
768023                  False  manual_static_filter  

[768024 rows x 5 columns]

In [44]:
tenant_id = '1'

def concatenate_names(names):
    return ', '.join(names)
    
target_example =display_databases(tenant_id, "target_information")

target_example['target_name'] = target_example['target_name'].fillna('').str.lower()


target_example['jeune'] = target_example['target_name'].str.contains('|'.join(['jeune', 'pass_culture']), case=False).astype(int)
target_example['optin'] = target_example['target_name'].str.contains('|'.join(['optin' ,'opt-in']), case=False).astype(int)
target_example['optout'] = target_example['target_name'].str.contains('|'.join(['optout']), case=False).astype(int)
target_example['scolaire'] = target_example['target_name'].str.contains('|'.join(['scolaire' , 'enseignant', 'chercheur', 'schulen', 'école']), case=False).astype(int)
target_example['entreprise'] = target_example['target_name'].str.contains('|'.join(['b2b']), case=False).astype(int)
target_example['famille'] = target_example['target_name'].str.contains('|'.join(['famille', 'enfants']), case=False).astype(int)
target_example['newsletter'] = target_example['target_name'].str.contains('|'.join(['nl', 'newsletter']), case=False).astype(int)



target_agg = target_example.groupby('customer_id').agg(
    nb_targets=('target_name', 'nunique'),  # Utilisation de tuples pour spécifier les noms de colonnes
    all_targets=('target_name', concatenate_names),
    all_target_types=('target_type_name', concatenate_names)
).reset_index()
target_agg

File path :  projet-bdc2324-team1/0_Input/Company_1/target_information.csv


customer_id  nb_targets  \
0                 1          28   
1                 2           7   
2                 3          11   
3                 4           6   
4                 5           4   
...             ...         ...   
151154      1256136           1   
151155      1256137           1   
151156      1256138           3   
151157      1256139           3   
151158      1256140           2   

                                              all_targets  \
0       consentement optin jeune public, DDCP rentrée ...   
1       consentement optin jeune public, consentement ...   
2       traversee du port de commerce (gagnant et perd...   
3       Arenametrix_bascule tel vers sib, consentement...   
4       Arenametrix_bascule tel vers sib, consentement...   
...                                                   ...   
151154                             consentement optin b2c   
151155                             consentement optin b2c   
151156  Inscrits NL jeune public site web, Inscrits NL...   
151157  Inscrits NL jeune public site web, Inscrits NL...   
151158               DRE MucemLab, consentement optin dre   

                                         all_target_types  
0       manual_static_filter, manual_static_filter, ma...  
1       manual_static_filter, manual_static_filter, ma...  
2       manual_static_filter, manual_static_filter, ma...  
3       manual_static_filter, manual_static_filter, ma...  
4       manual_static_filter, manual_static_filter, ma...  
...                                                   ...  
151154                               manual_static_filter  
151155                               manual_static_filter  
151156  manual_static_filter, manual_static_filter, ma...  
151157  manual_static_filter, manual_static_filter, ma...  
151158         manual_static_filter, manual_static_filter  

[151159 rows x 4 columns]

In [37]:
export_in_temporary(target_agg, 'Target_kpi_concatenate')

Export of dataset : Target_kpi_concatenate


In [ ]:
v

In [ ]:

def display_covering_time(df, company, datecover):
    """
    This function draws the time coverage of each company
    """
    min_date = df['purchase_date'].min().strftime("%Y-%m-%d")
    max_date = df['purchase_date'].max().strftime("%Y-%m-%d")
    datecover[company] = [datetime.strptime(min_date, "%Y-%m-%d") + timedelta(days=x) for x in range((datetime.strptime(max_date, "%Y-%m-%d") - datetime.strptime(min_date, "%Y-%m-%d")).days)]
    print(f'Couverture Company {company} : {min_date} - {max_date}')
    return datecover


def compute_time_intersection(datecover):
    """
    This function returns the time coverage for all companies
    """
    timestamps_sets = [set(timestamps) for timestamps in datecover.values()]
    intersection = set.intersection(*timestamps_sets)
    intersection_list = list(intersection)
    formated_dates = [dt.strftime("%Y-%m-%d") for dt in intersection_list]
    return sorted(formated_dates)


def df_coverage_modelization(sport, coverage_features = 0.7):
    """
    This function returns start_date, end_of_features and final dates
    that help to construct train and test datasets
    """
    datecover = {}
    for company in sport:
        df_products_purchased_reduced = display_input_databases(company, file_name = "products_purchased_reduced",
                                                          datetime_col = ['purchase_date'])
        datecover = display_covering_time(df_products_purchased_reduced, company, datecover)
    #print(datecover.keys())
    dt_coverage = compute_time_intersection(datecover)
    start_date = dt_coverage[0]
    end_of_features = dt_coverage[int(0.7 * len(dt_coverage))]
    final_date = dt_coverage[-1]
    return start_date, end_of_features, final_date
 

# Bases non communes : mise à plat

In [11]:
companies = {'musee' : ['1', '2', '3', '4'],
            'sport': ['5', '6', '7', '8', '9'],
            'musique' : ['10', '11', '12', '13', '14']}

all_companies = ['1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14']

In [15]:
companies_databases = pd.DataFrame()

for i in all_companies:
    company_databases = pd.DataFrame({'company_number' : [i]})

    BUCKET = "bdc2324-data/"+i
    for base in fs.ls(BUCKET):
        match = re.search(r'\/(\d+)\/(\d+)([a-zA-Z_]+)\.csv$', base)
        if match:
            nom_base = match.group(3)
            company_databases[nom_base] = 1

    companies_databases = pd.concat([companies_databases, company_databases])

In [20]:
pd.set_option("display.max_columns", None)
companies_databases


company_number  campaign_stats  campaigns  categories  countries  \
0              1               1          1           1          1   
0              2               1          1           1          1   
0              3               1          1           1          1   
0              4               1          1           1          1   
0              5               1          1           1          1   
0              6               1          1           1          1   
0              7               1          1           1          1   
0              8               1          1           1          1   
0              9               1          1           1          1   
0             10               1          1           1          1   
0             11               1          1           1          1   
0             12               1          1           1          1   
0             13               1          1           1          1   
0             14               1          1           1          1   

   currencies  customer_target_mappings  customersplus  event_types  events  \
0           1                         1              1            1       1   
0           1                         1              1            1       1   
0           1                         1              1            1       1   
0           1                         1              1            1       1   
0           1                         1              1            1       1   
0           1                         1              1            1       1   
0           1                         1              1            1       1   
0           1                         1              1            1       1   
0           1                         1              1            1       1   
0           1                         1              1            1       1   
0           1                         1              1            1       1   
0           1                         1              1            1       1   
0           1                         1              1            1       1   
0           1                         1              1            1       1   

   facilities  link_stats  pricing_formulas  product_packs  products  \
0           1           1                 1              1         1   
0           1           1                 1              1         1   
0           1           1                 1              1         1   
0           1           1                 1              1         1   
0           1           1                 1              1         1   
0           1           1                 1              1         1   
0           1           1                 1              1         1   
0           1           1                 1              1         1   
0           1           1                 1              1         1   
0           1           1                 1              1         1   
0           1           1                 1              1         1   
0           1           1                 1              1         1   
0           1           1                 1              1         1   
0           1           1                 1              1         1   

   products_groups  purchases  representation_category_capacities  \
0                1          1                                   1   
0                1          1                                   1   
0                1          1                                   1   
0                1          1                                   1   
0                1          1                                   1   
0                1          1                                   1   
0                1          1                                   1   
0                1          1                                   1   
0                1          1                                  

In [21]:
pd.reset_option("display.max_columns")

# Debut Travail 25/02

## Base communes au types Musée

In [ ]:
companies['musee']

In [ ]:
for i in companies['musique']:
    BUCKET = "bdc2324-data/"+i
    liste_base = []
    for base in fs.ls(BUCKET):
        match = re.search(r'\/(\d+)\/(\d+)([a-zA-Z_]+)\.csv$', base)
        if match:
            nom_base = match.group(3)
            liste_base.append(nom_base)
    globals()['base_'+i] = liste_base


In [ ]:
# Trouver l'intersection entre les cinq listes
intersection = set(base_1).intersection(base_2, base_3, base_4, base_101)

# Convertir le résultat en liste si nécessaire
intersection_liste = list(intersection)

print(intersection_liste)

In [ ]:
# Trouver l'intersection entre les cinq listes
intersection = set(base_10).intersection(base_12, base_13, base_14, base_11)

# Convertir le résultat en liste si nécessaire
intersection_liste = list(intersection)

print(intersection_liste)

In [ ]:
len(intersection_liste)

In [ ]:
df1_tags = load_dataset_2("1", "tags")

In [ ]:
df1_structure_tag_mappings = load_dataset_2("1", 'structure_tag_mappings')

In [ ]:
df1_customersplus = load_dataset_2("1", "customersplus")

In [ ]:
df1_customersplus.groupby('structure_id')['id'].count().reset_index().sort_values('id', ascending=False).head(20)

In [ ]:
df1_customersplus['structure_id'].isna().sum() / len(df1_customersplus['structure_id'])

In [ ]:
len(df1_structure_tag_mappings)

In [ ]:
df1_structure_tag_mappings.groupby('tag_id')['structure_id'].count().reset_index().sort_values('structure_id', ascending=False).head(20)

In [ ]:
?np.sort_values()

In [ ]:
def info_colonnes_dataframe(df):
    # Créer une liste pour stocker les informations sur chaque colonne
    infos_colonnes = []

    # Parcourir les colonnes du DataFrame
    for nom_colonne, serie in df.items():  # Utiliser items() au lieu de iteritems()
        # Calculer le taux de valeurs manquantes
        taux_na = serie.isna().mean() * 100

        # Ajouter les informations à la liste
        infos_colonnes.append({
            'Nom_colonne': nom_colonne,
            'Type_colonne': str(serie.dtype),
            'Taux_NA': taux_na
        })

    # Créer une nouvelle DataFrame à partir de la liste d'informations
    df_infos_colonnes = pd.DataFrame(infos_colonnes)

    return df_infos_colonnes

In [ ]:
info_colonnes_dataframe(df1_tags)

In [ ]:
info_colonnes_dataframe(df1_structure_tag_mappings)

In [ ]:
pd.set_option('display.max_colwidth', None)

print(df1_tags['name'])

In [ ]:
pd.set_option('display.max_rows', None)

In [ ]:
print(df1_tags['name'])

## KPI sur target_type

In [ ]:
pd.set_option('display.max_colwidth', None)


Raisonnement : on prends les target_type qui représente 90% des clients et on fait des catégories dessus.

In [ ]:
targets = load_dataset_2("3", "targets")
target_types = load_dataset_2("3", "target_types")

# target_all = pd.merge(targets, target_types, left_on= 'target_type_id', right_on= 'id' ,how = 'inner')


In [42]:
def print_main_target(tenant_id, nb_print = 40):
    df_target = display_databases(tenant_id, "target_information")

    print('Nombre de ciblage : ', len(df_target))
    nb_customers = df_target['customer_id'].nunique()
    print('Nombre de client avec étiquette target : ', nb_customers) 

    nb_custumers_per_target = df_target.groupby("target_name")['customer_id'].count().reset_index().sort_values('customer_id', ascending=False)
    nb_custumers_per_target['cumulative_customers'] = nb_custumers_per_target['customer_id'].cumsum()/len(df_target)
    nb_custumers_per_target['customer_id'] = nb_custumers_per_target['customer_id']/nb_customers

    return nb_custumers_per_target.head(nb_print)

In [47]:
pd.set_option("max_colwidth", None)
print_main_target('1', 60)

File path :  projet-bdc2324-team1/0_Input/Company_1/target_information.csv
Nombre de ciblage :  768024
Nombre de client avec étiquette target :  151159


target_name  \
161                        consentement optin mediation specialisee   
160                                 consentement optin jeune public   
158                                          consentement optin b2c   
5                                  Arenametrix_bascule tel vers sib   
165                                         consentement optout b2c   
19                            COM Inscrits NL générale (historique)   
162                          consentement optin newsletter generale   
169                         consentement optout newsletter generale   
170                                   consentement optout scolaires   
166                                         consentement optout dre   
164                                         consentement optout b2b   
126     Inscrits NL générale (export_291019 + operation_videomaton)   
157                                          consentement optin b2b   
216                                       ddcp_visiteurs dps 010622   
20                                          Contacts_prenomsdoubles   
115                           FORMATION _ acheteurs optin last year   
214                   ddcp_promo_visiteurs occasionnels_musee_8mois   
189                                  ddcp_promo_md_musée_dps 011019   
188                    ddcp_promo_MD_billet_musée_oct_2019_agarder2   
163                                    consentement optin scolaires   
159                                          consentement optin dre   
34                                      DDCP Newsletter enseignants   
36                                     DDCP Newsletter jeune public   
127                                   Inscrits NL générale site web   
145                                            Votre première liste   
61                                             DDCP billets famille   
106                                                    DRE MucemLab   
39                              DDCP Newsletter relais champ social   
110                                             DRE institutionnels   
48            DDCP PROMO Participants ateliers (adultes et enfants)   
74                                DDCP promo Plan B 2019 (concerts)   
72                           DDCP promo MD pass musées dps oct 2018   
94                                     DDCP rentrée culturelle 2023   
23                                         DDCP MD Procès du Siècle   
186                                 ddcp_md_scene_ouverte_au_talent   
108                                                  DRE chercheurs   
220                                             festival_jean_rouch   
105                                         DRE Festival Jean Rouch   
275                               structures_etiquette champ social   
86   DDCP promo spectateurs prog 21-22 (spectacles, ciné, ateliers)   
128                               Inscrits NL jeune public site web   
260                                               rappel po barvalo   
104                                        DDCP_marseille_jazz_2023   
32                               DDCP Newsletter centres de loisirs   
13                                        Autres_interet_exposition   
228                    import_arenametrix_contactstousecardouv_expo   
117                                       Formation clients fidèles   
22                                                   DDCP Cine 2023   
40                                                  DDCP OLBJ! 2023   
240                           journee-de-l-inclusion_20230601_21h25   
137                          Questionnaire 2 satisfaction scolaire    
93                     DDCP rendez-vous de septembre offre spéciale   
135                                           Plan B 2018 (électro)   
270                                         save_the_date_populaire   
132                                     Newsletter CCR (passerelle)   
116      Fichier institutionnel (ne pas utiliser sans autorisation)   
222      

In [48]:
print_main_target('2', 25)

File path :  projet-bdc2324-team1/0_Input/Company_2/target_information.csv
Nombre de ciblage :  260283
Nombre de client avec étiquette target :  233320


target_name  customer_id  \
13         Schokoladentour & Führungen Individuals     0.927906   
3                          Chocolateria Kurse 2023     0.073963   
16   mailxpert_contacts_2023-07-18_12-04-00 langue     0.025519   
15          mailxpert_contacts_2023-07-18_12-04-00     0.025519   
8                      Newsletter opt-in Allgemein     0.022836   
12   Schokoladentour & Führungen Gruppen / Schulen     0.011555   
5                                    Newsletter DE     0.010749   
7                                    Newsletter FR     0.008520   
6                                    Newsletter EN     0.004286   
4                      Frauen in Zürich - Schulung     0.001003   
17  mailxpert_contacts_2023-07-18_13-25-45_inaktiv     0.000471   
11                               Opt-in-Website DE     0.000030   
9                                Opt-in Website EN     0.000009   
10                               Opt-in Website FR     0.000004   
14                            Votre première liste     0.000004   
1                             Activated contact EN     0.000004   
2                             Activated contact FR     0.000004   
0                             Activated contact DE     0.000004   

    cumulative_customers  
13              0.831783  
3               0.898084  
16              0.920959  
15              0.943834  
8               0.964304  
12              0.974662  
5               0.984298  
7               0.991936  
6               0.995778  
4               0.996677  
17              0.997099  
11              0.997126  
9               0.997134  
10              0.997138  
14              0.997142  
1               0.997145  
2               0.997149  
0               0.997153

In [56]:
print_main_target('3', 70)

File path :  projet-bdc2324-team1/0_Input/Company_3/target_information.csv
Nombre de ciblage :  1617362
Nombre de client avec étiquette target :  257018


target_name  customer_id  \
67                                      MKG_NLmensuelle_2021_OK     0.972348   
66                                         MKG_NLmensuelle_2021     0.956007   
119                                            consent_optin_nl     0.636648   
115                                       consent_optin_general     0.602506   
78                                            Mkg_NL_mensuelle3     0.404162   
125                                      consent_optout_general     0.368126   
104                                                TEST LOCBASE     0.350532   
68                                  MKG_Non_inscrit_liste_08-22     0.310605   
116                            consent_optin_general_HISTORIQUE     0.301345   
80                                                   Mkg_Zone_C     0.135298   
7                          Acheteurs_100km_visite_depuismax5ans     0.091149   
54                               Inscription NL ancien site web     0.083477   
112                                      consent_optin_equestre     0.083216   
79                                                   Mkg_Zone_B     0.079889   
65                                 MKG_2022_ZoneB&ZoneC_Famille     0.072536   
111                                           consent_optin_b2b     0.064388   
102                                           Soft_Bounce_yahoo     0.064182   
100                                       Scénario Anniversaire     0.051249   
37                      B2B_scolaire_et_centres_de_loisirs_2023     0.046732   
20                                           B2B_Sans étiquette     0.040472   
122                                     consent_optout_equestre     0.038865   
17                            B2B_Inscrits newsletter Scolaires     0.038075   
28                          B2B_historique_newsletter_SCOLAIRES     0.038040   
118                                           consent_optin_jdp     0.036110   
76                                         MKG_aire cantilienne     0.031908   
21                                     B2B_Sans étiquette FR+BE     0.029165   
108                                       b2b - écoles mai 2021     0.028574   
86                                         Ouvreur_NL_juin_2021     0.018193   
126                                          consent_optout_jdp     0.016816   
127                                           consent_optout_nl     0.016633   
13                                                  B2B_CE_2023     0.016489   
106                      Visiteurs Aout-Sept sans questionnaire     0.016275   
89                             Pass Annuel en cours de validité     0.011540   
114                                   consent_optin_expositions     0.011388   
22                                B2B_Sans étiquette hors FR+BE     0.011307   
113                                    consent_optin_evenements     0.011240   
32                                   B2B_liste_à_requalifier_CE     0.010742   
110                           consent_optin_abonnes_passannuels     0.009665   
152                   liste mécènes donateurs 01012023-31102023     0.008746   
34                            B2B_liste_à_requalifier_SCOLAIRES     0.008688   
153                                    liste newsletter mécénat     0.008606   
144  liste des donateurs iraiser don ponctuel 10122020-20012022     0.007591   
134                                 don ponctuel iRaiser 250122     0.007587   
77                                        MKG_visiteurs_juin_ES     0.007498   
72                              MKG_acheteurs_domaine_noel_2021     0.006758   
6                      Acheteurs Journées des Plantes oct. 2022     0.006038   
96                       Réponse au formulaire de satisfaction      0.005871   
15                B2B_Inscrits newsletter Collectivités et CSE      0.005786   
26                                 B2B_historique_newsletter_CE     0.005735   
70                           MKG_acheteurs_1mois_pas

In [54]:
pd.set_option('display.max_rows', None)


In [57]:
print_main_target('4', 100)

File path :  projet-bdc2324-team1/0_Input/Company_4/target_information.csv
Nombre de ciblage :  4627640
Nombre de client avec étiquette target :  320813


target_name  \
232                                     Tous les contacts mis à jour   
76                                                     Base données    
191                                              Office de Tourisme    
128                                                Globale sans VIP    
112                                              Contacts structures   
98                                         Cible gratuité IMA COMEDY   
23                                      2 IEME ENVOI IMA COMEDY CLUB   
64                                     Actions Marketing ARABOFOLIES   
171                                           Liste globale sans VIP   
126            Formulaire inscription mallette "Cultures en partage"   
78                                            CAMPAGNE ADHESION 2023   
234                                                  Tous les optins   
192                                                       Optin 2023   
170                                   Liste globale optin-15-01-2021   
10                                                   10-03-sb-dolist   
195                                                  Origine - Nouba   
158                               LIVE2022_Intérêt Expositions musée   
414                                    old_Intéressés par la Musique   
415                                                old_Intérêt Danse   
100                                       Cible offre DAOUD DEPARDON   
12                                             13-04-2022-vente 2021   
73                                          Arabofolies Juillet 2022   
137                                                   Intérêt LGBTQ+   
274                                                  blacklistés ima   
208                                             Public traditionnel    
159                                          LIVE2022_Intérêt Humour   
99                                               Cible jeunes humour   
213                                 Relance gratuité IMA COMEDY CLUB   
101                                       Cible rencontres et débats   
189                                     Nouveaux inscrits newsletter   
349                                           interet nuit du cinéma   
141                        Intérêt prononcé pour la nuit du ramadan    
87                                                    Cible Algérie    
93                                  Cible News offre spéciale humour   
140                                          Intérêt musique électro   
280                                     cible Histoire et feminisme    
174                              Liste relais pour présentation 2023   
138                                        Intérêt musique Orientale   
18                                           16-07-21-nuit-du-cinema   
204                                  Profil Client Expos Divas (Geo)   
265                                       araborolies/Divas/relance    
203                                         Profil Client Expo Divas   
233  Tous les inscrits aux newsletters via le formulaire du site web   
243                                                     VIP Générale   
226                                             Strcutures sans VIP    
67                                                    Agi pour buren   
144                         Invitation à l'exposition Palestine LANG   
62           Acheteurs individuels de l'expo Juifs d'orient statique   
61                    Acheteurs individuels de l'expo Juifs d'orient   
95                                        Cible arabic Sound system    
244                                                     VIP STATIQUE   
245                                               VIP Téléchargement   
102                                              Cible scolaire 2022   
90                                                       Cible Maroc   
91                                                      Cible Maroc    
41                       

In [ ]:
print_main_target('101', 100)

## KPI sur tags

In [28]:
customersplus = load_dataset_2("4", "customersplus")[['id', 'structure_id']]

In [35]:
structure_tag_mappings = load_dataset_2('4', "structure_tag_mappings")[['structure_id', 'tag_id']]

In [34]:
customersplus[customersplus['structure_id'].notna()]['structure_id'].nunique()

19427

In [32]:
len(customersplus[customersplus['structure_id'].notna()])

33645

In [36]:
structure_tag_mappings['structure_id'].nunique()

3431

In [26]:
def tags_information(tenant_id, first_tags):

    customersplus = load_dataset_2(tenant_id, "customersplus")[['id', 'structure_id']]
    customersplus.rename(columns = {'id' : 'customer_id'}, inplace = True)
    tags = load_dataset_2(tenant_id, "tags")[['id', 'name']]
    tags.rename(columns = {'id' : 'tag_id', 'name' : 'tag_name'}, inplace = True)
    structure_tag_mappings = load_dataset_2(tenant_id, "structure_tag_mappings")[['structure_id', 'tag_id']]
    
    customer_tags = pd.merge(customersplus, structure_tag_mappings, on = 'structure_id', how = 'left')
    customer_tags = pd.merge(customer_tags, tags, on = 'tag_id', how = 'inner')
    
    nb_customers_with_tag = customer_tags['customer_id'].nunique()
    
    print('Nombre de client avec tag : ', nb_customers_with_tag)
    print('Proportion de clients avec tags : ', nb_customers_with_tag/len(customersplus))
    print('Moyenne de tags par client : ', len(customer_tags)/nb_customers_with_tag)
    
    info = customer_tags.groupby(['tag_id', 'tag_name'])['customer_id'].count().reset_index().sort_values('customer_id', ascending = False).head(first_tags)

    return info

In [37]:
tags_information("1", 20)

Nombre de client avec tag :  13320
Proportion de clients avec tags :  0.0877089012682233
Moyenne de tags par client :  2.1725975975975977


tag_id                                        tag_name  customer_id
1   11029.0                                     individuels         3270
18  11047.0                               groupes scolaires         2417
4   11033.0                                     association         2308
0   11028.0                          structures culturelles         2011
22  11051.0                      etablissement ens scolaire         1732
7   11036.0                                    champ social         1603
43  11072.0                             etab d'enseignement         1036
14  11043.0                            etablissement public          935
6   11035.0                           organisme de tourisme          892
16  11045.0                               centre de loisirs          864
44  11073.0                         musée, site & fondation          786
24  11053.0                               groupes etudiants          758
3   11032.0                                      entreprise          750
10  11039.0                    etablissement d'enseignement          741
5   11034.0                                asso. culturelle          692
15  11044.0                  administration et collectivité          676
17  11046.0                                  tour opérateur          642
19  11048.0                                     entreprises          515
72  11619.0  structures culturelles;musée, site & fondation          427
8   11037.0                                        handicap          426

In [43]:
tags_information("2", 20)

Nombre de client avec tag :  5953
Proportion de clients avec tags :  0.021598421025897787
Moyenne de tags par client :  1.0


tag_id        tag_name  customer_id
0     1.0  training-sb-ax            5

In [39]:
load_dataset_2("2", "tags")[['id', 'name']]

id            name
0   1  training-sb-ax
1   2             NaN

In [42]:
tags_information("3", 20)

Nombre de client avec tag :  23659
Proportion de clients avec tags :  0.09207484608139978
Moyenne de tags par client :  3.0620482691576143


tag_id                                  tag_name  customer_id
164  44539.0                   *individuel/particulier        13148
30   26926.0                                        ce         3216
14    6995.0                                   college         2126
16    7028.0                                     lycee         1577
154  44524.0                                   iraiser         1453
2     6714.0                            ecole primaire         1200
155  44525.0                                        bp         1094
15    7024.0                         centre de loisirs         1080
153  44515.0                                entreprise          998
126  44039.0                     ca fondation d'aumale          891
152  44514.0                               particulier          838
36   43663.0                                 président          816
76   43703.0                                 directeur          812
158  44528.0                                        dc          807
54   43681.0                                présidente          805
149  44511.0                    entreprise (financier)          805
90   43718.0  conseillère régionale déléguée titulaire          804
40   43667.0                     directeur de l'agence          801
78   43705.0                               sous-préfet          798
100  43728.0                chargée de mission paysage          797

In [40]:
tags_information("4", 20)

Nombre de client avec tag :  10495
Proportion de clients avec tags :  0.03271416949025744
Moyenne de tags par client :  5.298427822772749


tag_id                                           tag_name  customer_id
147   298.0                                              jhima         4219
146   297.0                                   colloque algérie         3851
142   292.0                                               i&ma         3826
154   305.0                                 mardis de la philo         3674
150   301.0                                 le grand continant         3670
144   295.0                                          araborama         3669
155   306.0                                 marie descourtieux         3669
145   296.0                        c'était la guerre d'algérie         3669
141   291.0                                        araborama 3         3669
102   198.0  association de collectivités territoriales spé...         3669
143   294.0                                        arabofolies         3669
103   199.0  rassemble les 11 000 élus de toute la france a...         3669
2      50.0                                        association          463
6      54.0                                            collège          446
1      49.0                                              ecole          374
7      55.0                                              lycée          275
5      53.0                                      centre social          200
53    130.0                                   cultures et arts          141
3      51.0                                             mairie          136
13     64.0                                   formation_ima_ax           87

In [41]:
tags_information("101", 20)

Nombre de client avec tag :  532342
Proportion de clients avec tags :  0.18660686931118298
Moyenne de tags par client :  24.114082676174338


tag_id                    tag_name  customer_id
20   349.0            clients internet       517491
24   356.0        associations / clubs       495520
5     10.0           agence de voyages       493774
32   410.0        guides conférenciers       493378
26   360.0      groupe amis ou famille       493021
23   354.0            ce / entreprises       493016
8     17.0            association/club       493008
1      3.0           c.e. / entreprise       492656
6     11.0                     college       492552
13    69.0               tour operator       492549
4      9.0              ecole primaire       492540
31   379.0  parent goûter anniversaire       492468
30   364.0                institutions       492364
2      6.0                 institution       492321
18   186.0                autocaristes       492153
7     13.0      enseignement superieur       492131
25   359.0           hotels / campings       492078
42  7186.0                  individuel       491913
3      7.0       groupe amis / famille       491900
0      2.0             client internet       491896

## KPI product

In [12]:
tenant_id = "1"

df_product = display_databases(tenant_id, file_name = "products_purchased_reduced", datetime_col = ['purchase_date'])

df_product.head()

File path :  projet-bdc2324-team1/0_Input/Company_1/products_purchased_reduced.csv


ticket_id  customer_id  purchase_id  event_type_id   supplier_name  \
0   13070859        48187      5107462              4  vente en ligne   
1   13070860        48187      5107462              4  vente en ligne   
2   13070861        48187      5107462              4  vente en ligne   
3   13070862        48187      5107462              4  vente en ligne   
4   13070863        48187      5107462              4  vente en ligne   

              purchase_date  amount  is_full_price  name_event_types  \
0 2018-12-28 14:47:50+00:00     8.0          False  spectacle vivant   
1 2018-12-28 14:47:50+00:00     4.0          False  spectacle vivant   
2 2018-12-28 14:47:50+00:00     4.0          False  spectacle vivant   
3 2018-12-28 14:47:50+00:00     4.0          False  spectacle vivant   
4 2018-12-28 14:47:50+00:00     4.0          False  spectacle vivant   

  name_facilities    name_categories            name_events  name_seasons  \
0           mucem  indiv prog enfant  l'école des magiciens          2018   
1           mucem  indiv prog enfant  l'école des magiciens          2018   
2           mucem  indiv prog enfant  l'école des magiciens          2018   
3           mucem  indiv prog enfant  l'école des magiciens          2018   
4           mucem  indiv prog enfant  l'école des magiciens          2018   

             start_date_time              end_date_time  open  
0  2018-12-31 14:15:00+01:00  1901-01-01 00:09:21+00:09  True  
1  2018-12-31 14:15:00+01:00  1901-01-01 00:09:21+00:09  True  
2  2018-12-31 14:15:00+01:00  1901-01-01 00:09:21+00:09  True  
3  2018-12-31 14:15:00+01:00  1901-01-01 00:09:21+00:09  True  
4  2018-12-31 14:15:00+01:00  1901-01-01 00:09:21+00:09  True

In [24]:
nb_tickets_per_events = df_product.groupby(['name_event_types', 'name_events'])['ticket_id'].count().reset_index().sort_values('ticket_id', ascending = False)
nb_tickets_per_events['prop_tickets'] = round(nb_tickets_per_events['ticket_id']/len(df_product), 3)
nb_tickets_per_events

name_event_types                        name_events  ticket_id  \
118      offre muséale groupe    visite générale du mucem (1h30)      43814   
212  offre muséale individuel   visite autonome scolaires (2h00)      34423   
68       offre muséale groupe  visite autonome exposition (1h30)      26489   
210  offre muséale individuel     visite autonome adultes (2h00)      22065   
160      offre muséale groupe   visites des exterieurs scolaires      15595   
..                        ...                                ...        ...   
364          spectacle vivant   kay ! lettres à un poète disparu          1   
443          spectacle vivant                      mauvais genre          1   
375          spectacle vivant     la madre que parió a la música          1   
260          spectacle vivant  ali a les yeux bleus (dès 12 ans)          1   
484          spectacle vivant              rengaine (dès 12 ans)          1   

     prop_tickets  
118         0.024  
212         0.019  
68          0.015  
210         0.012  
160         0.009  
..            ...  
364         0.000  
443         0.000  
375         0.000  
260         0.000  
484         0.000  

[544 rows x 4 columns]

# Fin travail 25/02

# Exemple sur Company 1

## Chargement données

In [3]:
BUCKET = "bdc2324-data/1"
liste_database = fs.ls(BUCKET)

In [5]:
liste_database_select = ['suppliers', 'ticket', 'purchase', 'consumption', 'type_ofs']

# Filtrer la liste pour les éléments contenant au moins un élément de la liste à tester
liste_database_filtered = [element for element in liste_database if any(element_part in element for element_part in liste_database_select)]

# Afficher le résultat
print(liste_database_filtered)

In [6]:
# loop to create dataframes from liste
files_path = liste_database

client_number = files_path[0].split("/")[1]
df_prefix = "df" + str(client_number) + "_"

for i in range(len(files_path)) :
    current_path = files_path[i]
    with fs.open(current_path, mode="rb") as file_in:
        df = pd.read_csv(file_in)
        # the pattern of the name is df1xxx
        nom_dataframe = df_prefix + re.search(r'\/(\d+)\/(\d+)([a-zA-Z_]+)\.csv$', current_path).group(3)
        globals()[nom_dataframe] = df

<<<<<<< local <modified: >
/tmp/ipykernel_445/4081512283.py:10: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_in)
/tmp/ipykernel_15285/4081512283.py:10: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_in)
>>>>>>> remote <modified: >


## customersplus.csv

In [22]:
a = pd.DataFrame(df1_customersplus.info())

In [31]:
def info_colonnes_dataframe(df):
    # Créer une liste pour stocker les informations sur chaque colonne
    infos_colonnes = []

    # Parcourir les colonnes du DataFrame
    for nom_colonne, serie in df.items():  # Utiliser items() au lieu de iteritems()
        # Calculer le taux de valeurs manquantes
        taux_na = serie.isna().mean() * 100

        # Ajouter les informations à la liste
        infos_colonnes.append({
            'Nom_colonne': nom_colonne,
            'Type_colonne': str(serie.dtype),
            'Taux_NA': taux_na
        })

    # Créer une nouvelle DataFrame à partir de la liste d'informations
    df_infos_colonnes = pd.DataFrame(infos_colonnes)

    return df_infos_colonnes

In [35]:
def cleaning_date(df, column_name):
    """
    Nettoie la colonne spécifiée du DataFrame en convertissant les valeurs en datetime avec le format ISO8601.

    Parameters:
    - df: DataFrame
        Le DataFrame contenant la colonne à nettoyer.
    - column_name: str
        Le nom de la colonne à nettoyer.

    Returns:
    - DataFrame
        Le DataFrame modifié avec la colonne nettoyée.
    """
    df[column_name] = pd.to_datetime(df[column_name], utc = True, format = 'ISO8601')
    return df

In [32]:
a = info_colonnes_dataframe(df1_customersplus)

In [33]:
a

In [16]:
a = pd.DataFrame(df1_customersplus.isna().sum()/len(df1_customersplus)*100)

In [40]:
# Selection des variables
df1_customersplus_clean = df1_customersplus.copy()

cleaning_date(df1_customersplus_clean, 'first_buying_date')
cleaning_date(df1_customersplus_clean, 'last_visiting_date')

df1_customersplus_clean.drop(['lastname', 'firstname', 'email', 'civility', 'note', 'created_at', 'updated_at', 'deleted_at', 'extra', 'reference', 'extra_field', 'identifier', 'need_reload', 'preferred_category', 'preferred_supplier', 'preferred_formula', 'zipcode', 'last_visiting_date'], axis = 1, inplace=True)
df1_customersplus_clean.rename(columns = {'id' : 'customer_id'}, inplace = True)



## tickets.csv

In [6]:
df1_tickets

In [7]:
df1_tickets.info()

In [8]:
df1_tickets.isna().sum()/len(df1_tickets)*100

In [9]:
# Selection des variables
df1_tickets_clean = df1_tickets.drop(['lastname', 'firstname', 'email', 'created_at', 'updated_at', 'extra', 'reference', 'extra_field', 'identifier', 'need_reload', 'preferred_category', 'preferred_supplier', 'preferred_formula', 'zipcode'], axis = 1, inplace=True)
df1_tickets_clean.rename(columns = {'id' : 'customer_id'}, inplace = True)

## suppliers.csv

In [10]:
df1_suppliers

In [11]:
df1_suppliers.info()

In [12]:
df1_suppliers.isna().sum()/len(df1_suppliers)*100

In [13]:
# Selection des variables
df1_suppliers_clean = df1_suppliers[['id', 'name']]
df1_suppliers_clean.rename(columns = {'name' : 'supplier_name'}, inplace = True)

In [14]:
df1_suppliers_clean

## type_ofs.csv

In [15]:
df1_type_ofs

In [16]:
df1_type_ofs.info()

In [17]:
# Selection des variables
df1_type_ofs_clean = df1_type_ofs[['id', 'name', 'children']]
df1_type_ofs_clean.rename(columns = {'name' : 'type_of_ticket_name'}, inplace = True)

## purchases.csv

In [18]:
df1_purchases

In [19]:
df1_purchases.info()

In [20]:
# Nettoyage purchase_date
df1_purchases['purchase_date'] = pd.to_datetime(df1_purchases['purchase_date'], utc = True)
df1_purchases['purchase_date'] = pd.to_datetime(df1_purchases['purchase_date'], format = 'ISO8601')

In [21]:
df1_purchases.info()

In [22]:
# Selection des variables
df1_purchases_clean = df1_purchases[['id', 'purchase_date', 'customer_id']]

## Fusion de l'ensemble des données billétiques

In [23]:
# Fusion avec fournisseurs
df1_ticket_information = pd.merge(df1_tickets_clean, df1_suppliers_clean, left_on = 'supplier_id', right_on = 'id', how = 'inner')
df1_ticket_information.drop(['supplier_id', 'id'], axis = 1, inplace=True)

# Fusion avec type de tickets
df1_ticket_information = pd.merge(df1_ticket_information, df1_type_ofs_clean, left_on = 'type_of', right_on = 'id', how = 'inner')
df1_ticket_information.drop(['type_of', 'id'], axis = 1, inplace=True)

# Fusion avec achats
df1_ticket_information = pd.merge(df1_ticket_information, df1_purchases_clean, left_on = 'purchase_id', right_on = 'id', how = 'inner')
df1_ticket_information.drop(['purchase_id', 'id'], axis = 1, inplace=True)

In [24]:
df1_ticket_information

# Utilisation de fonctions

In [51]:
# Créer un DataFrame exemple
df_not_clean = df1_campaign_stats[['opened_at']].head(20)

# Appliquer la fonction pour nettoyer la colonne 'purchase_date' de manière vectorisée
df_clean = cleaning_date(df_not_clean, 'opened_at')
df_clean.rename(columns = {'opened_at' : 'opened_at_clean'}, inplace = True)

test = pd.concat([df1_campaign_stats[['opened_at']].head(20), df_clean], axis=1)

test.info()

## Nettoyage, selection et fusion

In [23]:
df1_ticket_information

In [14]:
df1_ticket_information.info()

# Customer information

## Target area

In [8]:
# Target.csv cleaning
df1_targets_clean = df1_targets[["id", "target_type_id", "name"]]
df1_targets_clean.rename(columns = {'id' : 'target_id' , 'name' : 'target_name'}, inplace = True)

# target_type cleaning
df1_target_types_clean = df1_target_types[["id","is_import","name"]].add_prefix("target_type_")

#customer_target_mappings cleaning
df1_customer_target_mappings_clean = df1_customer_target_mappings[["id", "customer_id", "target_id"]]

# Merge target et target_type
df1_targets_full = pd.merge(df1_targets_clean, df1_target_types_clean, left_on='target_type_id', right_on='target_type_id', how='inner')
df1_targets_full.drop(['target_type_id'], axis = 1, inplace=True)

# Merge
df1_targets_full = pd.merge(df1_customer_target_mappings_clean, df1_targets_full, left_on='target_id', right_on='target_id', how='inner')
df1_targets_full.drop(['target_id'], axis = 1, inplace=True)

/tmp/ipykernel_15285/2625134041.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1_targets_clean.rename(columns = {'id' : 'target_id' , 'name' : 'target_name'}, inplace = True)


In [62]:
df1_targets_test = df1_targets_full[['id', 'customer_id']].groupby(['customer_id']).count()
len(df1_targets_test[df1_targets_test['id'] > 1]) / len(df1_targets_test)

# 99,6% des 151 000 client visés sont catégorisés plusieurs fois et en moyenne 5 fois... 
df1_targets_test.mean()


In [10]:
df1_targets_full.head()

id  customer_id               target_name  target_type_is_import  \
0  1184824       645400  DDCP PROMO Réseau livres                  False   
1   210571         2412  DDCP PROMO Réseau livres                  False   
2   210572         4536  DDCP PROMO Réseau livres                  False   
3   210573         6736  DDCP PROMO Réseau livres                  False   
4   210574        38210  DDCP PROMO Réseau livres                  False   

       target_type_name  
0  manual_static_filter  
1  manual_static_filter  
2  manual_static_filter  
3  manual_static_filter  
4  manual_static_filter

In [14]:
# Catégorisation des target_name
import pandas as pd
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.probability import FreqDist

# Téléchargement des ressources nécessaires
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')



[nltk_data] Downloading package punkt to /home/onyxia/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /home/onyxia/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /home/onyxia/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [19]:
# Définition des fonctions de tokenisation, suppression des mots vides et lemmatisation
def preprocess_text(texte):
    # Concaténation des éléments de la liste en une seule chaîne de caractères
    texte_concat = ' '.join(texte)
    
    # Tokenisation des mots
    tokens = word_tokenize(texte_concat.lower())
    
    # Suppression des mots vides (stopwords)
    stop_words = set(stopwords.words('french'))
    filtered_tokens = [word for word in tokens if word not in stop_words]
    
    # Lemmatisation des mots
    lemmatizer = WordNetLemmatizer()
    lemmatized_tokens = [lemmatizer.lemmatize(word) for word in filtered_tokens]
    
    return lemmatized_tokens


# Appliquer le prétraitement à la colonne de texte
df1_targets_full['target_name_tokened'] = df1_targets_full['target_name'].apply(preprocess_text)

# Concaténer les listes de mots pour obtenir une liste de tous les mots dans le corpus
all_words = [word for tokens in df1_targets_full['target_name_tokened'] for word in tokens]

# Calculer la fréquence des mots
freq_dist = FreqDist(all_words)




Mots les plus fréquents:
consentement: 550777
optin: 463579
jeune: 155103
public: 155103
mediation: 150001


In [22]:
# Affichage des mots les plus fréquents
print("Mots les plus fréquents:")
for mot, freq in freq_dist.most_common(15):
    print(f"{mot}: {freq}")

Mots les plus fréquents:
consentement: 550777
optin: 463579
jeune: 155103
public: 155103
mediation: 150001
specialisee: 150001
b2c: 143432
optout: 97683
newsletter: 56022
(: 46084
): 46084
inscrits: 42296
nl: 42294
générale: 41037
generale: 40950


In [18]:
import pandas as pd
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer

# Téléchargement des ressources nécessaires
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

# Création de la DataFrame d'exemple
data = {'texte': ["Le chat noir mange une souris.", "Le chien blanc aboie."]}
df = pd.DataFrame(data)

# Fonction pour prétraiter le texte
def preprocess_text(texte):
    # Concaténation des éléments de la liste en une seule chaîne de caractères
    texte_concat = ' '.join(texte)
    
    # Tokenisation des mots
    tokens = word_tokenize(texte_concat.lower())
    
    # Suppression des mots vides (stopwords)
    stop_words = set(stopwords.words('french'))
    filtered_tokens = [word for word in tokens if word not in stop_words]
    
    # Lemmatisation des mots
    lemmatizer = WordNetLemmatizer()
    lemmatized_tokens = [lemmatizer.lemmatize(word) for word in filtered_tokens]
    
    return lemmatized_tokens

# Appliquer la fonction de prétraitement à la colonne de texte
df['texte_preprocessed'] = df['texte'].apply(preprocess_text)

# Afficher le résultat
print(df)


                            texte  \
0  Le chat noir mange une souris.   
1           Le chien blanc aboie.   

                                 texte_preprocessed  
0  [e, h, a, o, i, r, a, g, e, u, e, o, u, r, i, .]  
1              [e, h, i, e, b, a, a, b, o, i, e, .]  


[nltk_data] Downloading package punkt to /home/onyxia/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /home/onyxia/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /home/onyxia/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


## Campaign area

In [52]:
# campaign_stats cleaning 
df1_campaign_stats_clean = df1_campaign_stats[["id", "campaign_id", "customer_id", "opened_at", "sent_at", "delivered_at"]]
cleaning_date(df1_campaign_stats_clean, 'opened_at')
cleaning_date(df1_campaign_stats_clean, 'sent_at')
cleaning_date(df1_campaign_stats_clean, 'delivered_at')

# campaigns cleaning
df1_campaigns_clean = df1_campaigns[["id", "name", "service_id", "sent_at"]].add_prefix("campaign_")
cleaning_date(df1_campaigns_clean, 'campaign_sent_at')

# Merge 
df1_campaigns_full = pd.merge(df1_campaign_stats_clean, df1_campaigns_clean, on = "campaign_id", how = "left")
df1_campaigns_full.drop(['campaign_id'], axis = 1, inplace=True)

In [53]:
df1_campaigns_full.info()

In [56]:
df1_campaigns_information

## Link area

In [37]:
df1_campaigns

In [38]:
df1_link_stats

## Supplier

In [7]:
# Fonction d'exploration pour suppliers.csv = label itr et commission inconnues
def suppliers_exploration(suppliers = None) : 
    
    # Taux de NaN pour ces colonnes
    label_na = suppliers['label'].isna().sum()/len(suppliers)*100
    itr_na = suppliers['itr'].isna().sum()/len(suppliers)*100
    commission_na = suppliers['commission'].isna().sum()/len(suppliers)*100

    suppliers_desc = pd.DataFrame({'nb_suppliers' : [suppliers['name'].nunique()],
                                  'label_na' : [label_na],
                                  'itr_na' : [itr_na],
                                  'commission_na' : [commission_na]})

    return suppliers_desc

In [8]:
df1_suppliers_desc = suppliers_exploration(suppliers = df1_suppliers)

In [9]:
df1_suppliers_desc

nb_suppliers  label_na  itr_na  commission_na
0             9     100.0   100.0          100.0

In [10]:
BUCKET = "bdc2324-data"
liste_folders = fs.ls(BUCKET)

liste_files = []
for company_folder in liste_folders : 
    liste_files.extend(fs.ls(company_folder))

In [11]:
liste_database_select = ['suppliers']

# Filtrer la liste pour les éléments contenant au moins un élément de la liste à tester
liste_suppliers = [element for element in liste_files if any(element_part in element for element_part in liste_database_select)]

# Afficher le résultat
print(liste_suppliers)

['bdc2324-data/1/1suppliers.csv', 'bdc2324-data/10/10suppliers.csv', 'bdc2324-data/101/101suppliers.csv', 'bdc2324-data/11/11suppliers.csv', 'bdc2324-data/12/12suppliers.csv', 'bdc2324-data/13/13suppliers.csv', 'bdc2324-data/14/14suppliers.csv', 'bdc2324-data/2/2suppliers.csv', 'bdc2324-data/3/3suppliers.csv', 'bdc2324-data/4/4suppliers.csv', 'bdc2324-data/5/5suppliers.csv', 'bdc2324-data/6/6suppliers.csv', 'bdc2324-data/7/7suppliers.csv', 'bdc2324-data/8/8suppliers.csv', 'bdc2324-data/9/9suppliers.csv']


In [32]:
# loop to create dataframes from file 2
def database_loading(database_name = None):
    files_path = database_name
    
    client_number = files_path.split("/")[1]
    df_prefix = "df" + str(client_number) + "_"
    
    current_path = files_path
    with fs.open(current_path, mode="rb") as file_in:
        df = pd.read_csv(file_in)

    return df, client_number

In [45]:
df_all = pd.DataFrame()

for link in liste_suppliers:
    
    df_supplier, tenant_id = database_loading(link)
    
    df_supplier['tenant_id'] = int(tenant_id)

    df_all = pd.concat([df_all, df_supplier], axis = 0)
    

In [63]:
# df_all[df_all['tenant_id'] == 101]['name'].unique()

In [66]:
liste_mots = ['en ligne', 'internet', 'web', 'net', 'vad', 'online'] 
# vad = vente à distance
df_all['name'] = df_all['name'].fillna('')

df_all['canal_vente_internet'] = df_all['name'].str.contains('|'.join(liste_mots), case=False).astype(int)


In [68]:
df_all.groupby('tenant_id')['canal_vente_internet'].max()

tenant_id
1      1
2      1
3      1
4      1
5      1
6      1
7      1
8      1
9      1
10     1
11     1
12     1
13     1
14     1
101    1
Name: canal_vente_internet, dtype: int64